In [1]:
# Import libraries and dependencies
import numpy as np
import pandas as pd
from pathlib import Path
import hvplot
import hvplot.pandas
from IPython.display import Markdown

pd.set_option("display.max_rows", 2000)
pd.set_option("display.max_columns", 2000)
pd.set_option("display.width", 1000)

C:\Users\wazar\anaconda3\envs\algotrading\lib\site-packages\ipykernel\parentpoller.py:116: UserWarning: Parent poll failed.  If the frontend dies,
                the kernel may be left running.  Please let us know
                about your system (bitness, Python, etc.) at
                ipython-dev@scipy.org
  ipython-dev@scipy.org""")


In [2]:
# Set the file path
filepath = Path("Resources/Data/MSCI Europe.csv")

# Read the CSV located at the file path into a Pandas DataFrame
aapl_df = pd.read_csv(filepath, parse_dates=True, infer_datetime_format=True)

# Print the DataFrame
aapl_df.head()

Date   Close       Ticker
0  Dec-31-1969  100.00  MSCI Europe
1  Jan-07-1970  100.48  MSCI Europe
2  Jan-14-1970  101.20  MSCI Europe
3  Jan-21-1970  100.37  MSCI Europe
4  Jan-28-1970   99.91  MSCI Europe

In [3]:
### Generate a Dual Moving Average Crossover Trading Signal

In [4]:
# Grab just the `date` and `close` from the IEX dataset
signals_df = aapl_df.loc[:, ['Date', 'Close']].copy()

# Set the `date` column as the index
signals_df = signals_df.set_index("Date", drop=True)

# Set the short window and long windows
short_window = 50
long_window = 100

# Generate the short and long moving averages (50 and 100 days, respectively)
signals_df['SMA50'] = signals_df['Close'].rolling(window=short_window).mean()
signals_df['SMA100'] = signals_df['Close'].rolling(window=long_window).mean()
signals_df['Signal'] = 0.0

# Generate the trading signal 0 or 1,
# where 0 is when the SMA50 is under the SMA100, and
# where 1 is when the SMA50 is higher (or crosses over) the SMA100
signals_df['Signal'][short_window:] = np.where(
    signals_df['SMA50'][short_window:] > signals_df['SMA100'][short_window:], 1.0, 0.0
)

# Calculate the points in time at which a position should be taken, 1 or -1
signals_df['Entry/Exit'] = signals_df['Signal'].diff()

# Print the DataFrame
signals_df.tail(10)

Close      SMA50     SMA100  Signal  Entry/Exit
Date                                                          
Dec-31-2020  1840.22  1736.2796  1682.8153     1.0         0.0
Jan-01-2021  1840.22  1740.7170  1684.7898     1.0         0.0
Jan-04-2021  1858.37  1746.1254  1686.8390     1.0         0.0
Jan-05-2021  1855.93  1751.7552  1688.8796     1.0         0.0
Jan-06-2021  1882.84  1759.0542  1691.1056     1.0         0.0
Jan-07-2021  1889.17  1766.7654  1693.6590     1.0         0.0
Jan-08-2021  1901.16  1774.6918  1696.4455     1.0         0.0
Jan-11-2021  1872.80  1781.5904  1698.6387     1.0         0.0
Jan-12-2021  1875.21  1787.5786  1700.8952     1.0         0.0
Jan-13-2021  1877.03  1793.0274  1703.0354     1.0         0.0

In [5]:
### Plot Entry and Exit Points of Dual Moving Average Crossover Trading Strategy

In [6]:
# Visualize exit position relative to close price
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Close'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize entry position relative to close price
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Close'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize close price for the investment
security_close = signals_df[['Close']].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Visualize moving averages
moving_avgs = signals_df[['SMA50', 'SMA100']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I          :Curve   [Date]   (Close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.Close.I  :Scatter   [Date]   (Close)
   .Scatter.Close.II :Scatter   [Date]   (Close)

In [7]:
### Backtest the Trading Strategy

In [8]:
# Set initial capital
initial_capital = float(100000)

# Set the share size
share_size = 500

# Take a 500 share position where the dual moving average crossover is 1 (SMA50 is greater than SMA100)
signals_df['Position'] = share_size * signals_df['Signal']

# Find the points in time where a 500 share position is bought or sold
signals_df['Entry/Exit Position'] = signals_df['Position'].diff()

# Multiply share price by entry/exit positions and get the cumulatively sum
signals_df['Portfolio Holdings'] = signals_df['Close'] * signals_df['Entry/Exit Position'].cumsum()

# Subtract the initial capital by the portfolio holdings to get the amount of liquid cash in the portfolio
signals_df['Portfolio Cash'] = initial_capital - (signals_df['Close'] * signals_df['Entry/Exit Position']).cumsum()

# Get the total portfolio value by adding the cash amount by the portfolio holdings (or investments)
signals_df['Portfolio Total'] = signals_df['Portfolio Cash'] + signals_df['Portfolio Holdings']

# Calculate the portfolio daily returns
signals_df['Portfolio Daily Returns'] = signals_df['Portfolio Total'].pct_change()

# Calculate the cumulative returns
signals_df['Portfolio Cumulative Returns'] = (1 + signals_df['Portfolio Daily Returns']).cumprod() - 1

# Print the DataFrame
signals_df.tail(10)

Close      SMA50     SMA100  Signal  Entry/Exit  Position  Entry/Exit Position  Portfolio Holdings  Portfolio Cash  Portfolio Total  Portfolio Daily Returns  Portfolio Cumulative Returns
Date                                                                                                                                                                                                     
Dec-31-2020  1840.22  1736.2796  1682.8153     1.0         0.0     500.0                  0.0            920110.0         21945.0         942055.0                -0.008170                       8.42055
Jan-01-2021  1840.22  1740.7170  1684.7898     1.0         0.0     500.0                  0.0            920110.0         21945.0         942055.0                 0.000000                       8.42055
Jan-04-2021  1858.37  1746.1254  1686.8390     1.0         0.0     500.0                  0.0            929185.0         21945.0         951130.0                 0.009633                       8.51130
Jan-05-2021  1855.93  1751.7552  1688.8796     1.0         0.0     500.0                  0.0            927965.0         21945.0         949910.0                -0.001283                       8.49910
Jan-06-2021  1882.84  1759.0542  1691.1056     1.0         0.0     500.0                  0.0            941420.0         21945.0         963365.0                 0.014164                       8.63365
Jan-07-2021  1889.17  1766.7654  1693.6590     1.0         0.0     500.0                  0.0            944585.0         21945.0         966530.0                 0.003285                       8.66530
Jan-08-2021  1901.16  1774.6918  1696.4455     1.0         0.0     500.0                  0.0            950580.0         21945.0         972525.0                 0.006203                       8.72525
Jan-11-2021  1872.80  1781.5904  1698.6387     1.0         0.0     500.0                  0.0            936400.0         21945.0         958345.0                -0.014581                       8.58345
Jan-12-2021  1875.21  1787.5786  1700.8952     1.0         0.0     500.0                  0.0            937605.0         21945.0         959550.0                 0.001257                       8.59550
Jan-13-2021  1877.03  1793.0274  1703.0354     1.0         0.0     500.0                  0.0            938515.0         21945.0         960460.0                 0.000948                       8.60460

In [9]:
### Plot Entry/Exit Points of Trading Strategy vs. Backtest Results

In [10]:
# Visualize exit position relative to total portfolio value
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Portfolio Total'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize entry position relative to total portfolio value
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Portfolio Total'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize total portoflio value for the investment
total_portfolio_value = signals_df[['Portfolio Total']].hvplot(
    line_color='lightgray',
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Overlay plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I                    :Curve   [Date]   (Portfolio Total)
   .Scatter.Portfolio_Total.I  :Scatter   [Date]   (Portfolio Total)
   .Scatter.Portfolio_Total.II :Scatter   [Date]   (Portfolio Total)

In [11]:
### Prepare Portfolio Evaluation Metrics DataFrame

In [12]:
# Prepare DataFrame for metrics
metrics = [
    'Annual Return',
    'Cumulative Returns',
    'Annual Volatility',
    'Sharpe Ratio',
    'Sortino Ratio']

columns = ['Backtest']

# Initialize the DataFrame with index set to evaluation metrics and column as `Backtest` (just like PyFolio)
portfolio_evaluation_df = pd.DataFrame(index=metrics, columns=columns)
portfolio_evaluation_df

Backtest
Annual Return           NaN
Cumulative Returns      NaN
Annual Volatility       NaN
Sharpe Ratio            NaN
Sortino Ratio           NaN

In [13]:
### Calculate and Assign Portfolio Evaluation Metrics

In [14]:
# Calculate cumulative return
portfolio_evaluation_df.loc['Cumulative Returns'] = signals_df['Portfolio Cumulative Returns'][-1]

# Calculate annualized return
portfolio_evaluation_df.loc['Annual Return'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252
)

# Calculate annual volatility
portfolio_evaluation_df.loc['Annual Volatility'] = (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)

# Calculate Sharpe Ratio
portfolio_evaluation_df.loc['Sharpe Ratio'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252) / (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)

# Calculate Downside Return
sortino_ratio_df = signals_df[['Portfolio Daily Returns']].copy()
sortino_ratio_df.loc[:,'Downside Returns'] = 0

target = 0
mask = sortino_ratio_df['Portfolio Daily Returns'] < target
sortino_ratio_df.loc[mask, 'Downside Returns'] = sortino_ratio_df['Portfolio Daily Returns']**2
portfolio_evaluation_df

# Calculate Sortino Ratio
down_stdev = np.sqrt(sortino_ratio_df['Downside Returns'].mean()) * np.sqrt(252)
expected_return = sortino_ratio_df['Portfolio Daily Returns'].mean() * 252
sortino_ratio = expected_return/down_stdev

portfolio_evaluation_df.loc['Sortino Ratio'] = sortino_ratio
portfolio_evaluation_df.head()

Backtest
Annual Return       0.0514685
Cumulative Returns     8.6046
Annual Volatility    0.120905
Sharpe Ratio         0.425692
Sortino Ratio        0.591828

In [15]:
### Prepare Trade Evaluation Metrics DataFrame

In [16]:
# Initialize trade evaluation DataFrame with columns
trade_evaluation_df = pd.DataFrame(
    columns=[
        'Stock', 
        'Entry Date', 
        'Exit Date', 
        'Shares', 
        'Entry Share Price', 
        'Exit Share Price', 
        'Entry Portfolio Holding', 
        'Exit Portfolio Holding', 
        'Profit/Loss']
)

trade_evaluation_df

Empty DataFrame
Columns: [Stock, Entry Date, Exit Date, Shares, Entry Share Price, Exit Share Price, Entry Portfolio Holding, Exit Portfolio Holding, Profit/Loss]
Index: []

In [17]:
### Generating Trade Evaluation Metrics

In [18]:
# Initialize iterative variables
entry_date = ''
exit_date = ''
entry_portfolio_holding = 0
exit_portfolio_holding = 0
share_size = 0
entry_share_price = 0
exit_share_price = 0

# Loop through signal DataFrame
# If `Entry/Exit` is 1, set entry trade metrics
# Else if `Entry/Exit` is -1, set exit trade metrics and calculate profit,
# Then append the record to the trade evaluation DataFrame
for index, row in signals_df.iterrows():
    if row['Entry/Exit'] == 1:
        entry_date = index
        entry_portfolio_holding = abs(row['Portfolio Holdings'])
        share_size = row['Entry/Exit Position']
        entry_share_price = row['Close']

    elif row['Entry/Exit'] == -1:
        exit_date = index
        exit_portfolio_holding = abs(row['Close'] * row['Entry/Exit Position'])
        exit_share_price = row['Close']
        profit_loss =  entry_portfolio_holding - exit_portfolio_holding
        trade_evaluation_df = trade_evaluation_df.append(
            {
                'Stock': 'MSCI Europe',
                'Entry Date': entry_date,
                'Exit Date': exit_date,
                'Shares': share_size,
                'Entry Share Price': entry_share_price,
                'Exit Share Price': exit_share_price,
                'Entry Portfolio Holding': entry_portfolio_holding,
                'Exit Portfolio Holding': exit_portfolio_holding,
                'Profit/Loss': profit_loss
            },
            ignore_index=True)

# Print the DataFrame
trade_evaluation_df

Stock   Entry Date    Exit Date  Shares  Entry Share Price  Exit Share Price  Entry Portfolio Holding  Exit Portfolio Holding  Profit/Loss
0   MSCI Europe  Jul-30-1971  Aug-02-1972   500.0             104.23            126.47                  52115.0                 63235.0     -11120.0
1   MSCI Europe  Sep-08-1972  Oct-11-1972   500.0             124.09            120.54                  62045.0                 60270.0       1775.0
2   MSCI Europe  Jan-18-1973  Aug-24-1973   500.0             121.78            123.98                  60890.0                 61990.0      -1100.0
3   MSCI Europe  Apr-08-1974  Jun-05-1974   500.0             105.22            100.92                  52610.0                 50460.0       2150.0
4   MSCI Europe  Jan-17-1975  Jul-21-1975   500.0              84.42            100.86                  42210.0                 50430.0      -8220.0
5   MSCI Europe  Nov-21-1975  Apr-14-1976   500.0             104.72            102.83                  52360.0                 51415.0        945.0
6   MSCI Europe  Jan-10-1977  Dec-20-1978   500.0              96.05            130.17                  48025.0                 65085.0     -17060.0
7   MSCI Europe  Feb-15-1979  Jul-05-1979   500.0             129.60            141.01                  64800.0                 70505.0      -5705.0
8   MSCI Europe  Aug-14-1979  Nov-20-1979   500.0             143.14            137.06                  71570.0                 68530.0       3040.0
9   MSCI Europe  Jan-30-1980  Apr-09-1980   500.0             148.54            131.41                  74270.0                 65705.0       8565.0
10  MSCI Europe  Jun-18-1980  Dec-23-1980   500.0             152.35            151.78                  76175.0                 75890.0        285.0
11  MSCI Europe  Dec-08-1981  Mar-15-1982   500.0             130.83            123.91                  65415.0                 61955.0       3460.0
12  MSCI Europe  Jun-15-1982  Jun-29-1982   500.0             120.73            114.53                  60365.0                 57265.0       3100.0
13  MSCI Europe  Oct-11-1982  Sep-05-1983   500.0             124.93            146.61                  62465.0                 73305.0     -10840.0
14  MSCI Europe  Dec-14-1983  Dec-19-1983   500.0             145.68            145.70                  72840.0                 72850.0        -10.0
15  MSCI Europe  Dec-22-1983  Jun-08-1984   500.0             148.03            154.81                  74015.0                 77405.0      -3390.0
16  MSCI Europe  Oct-11-1984  Jul-21-1986   500.0             145.41            311.76                  72705.0                155880.0     -83175.0
17  MSCI Europe  Aug-29-1986  Dec-17-1986   500.0             353.48            341.94                 176740.0                170970.0       5770.0
18  MSCI Europe  Jan-02-1987  Oct-29-1987   500.0             359.68            343.98                 179840.0                171990.0       7850.0
19  MSCI Europe  Mar-02-1988  Jul-06-1988   500.0             369.47            375.50                 184735.0                187750.0      -3015.0
20  MSCI Europe  Oct-31-1988  Jun-06-1989   500.0             402.76            409.26                 201380.0                204630.0      -3250.0
21  MSCI Europe  Jul-24-1989  Nov-10-1989   500.0             453.98            444.16                 226990.0                222080.0       4910.0
22  MSCI Europe  Dec-28-1989  Apr-17-1990   500.0             508.89            506.13                 254445.0                253065.0       1380.0
23  MSCI Europe  May-29-1990  Sep-18-1990   500.0             527.50            486.63                 263750.0                243315.0      20435.0
24  MSCI Europe  Jan-04-1991  Jan-07-1991   500.0             477.33            462.53                 238665.0                231265.0       7400.0
25  MSCI Europe  Jan-18-1991  Jan-28-1991   500.0             473.60            483.63                 236800.0                241815.0 

In [19]:
### Create Hvplot Line Chart of Closing, SMA50, and SMA100

In [20]:
price_df = signals_df[['Close', 'SMA50', 'SMA100']]
price_chart = price_df.hvplot.line()
price_chart.opts(xaxis=None)

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [21]:
### Create Hvplot Table of Portfolio Metrics

In [22]:
portfolio_evaluation_df.reset_index(inplace=True)
portfolio_evaluation_table = portfolio_evaluation_df.hvplot.table()
portfolio_evaluation_table

:Table   [index,Backtest]

In [23]:
### Create Hvplot Table of Trade Metrics  

In [24]:
trade_evaluation_table = trade_evaluation_df.hvplot.table()
trade_evaluation_table

:Table   [Stock,Entry Date,Exit Date,Shares,Entry Share Price,Exit Share Price,Entry Portfolio Holding,Exit Portfolio Holding,Profit/Loss]

In [25]:
### Build a Dashboard with `hvplot`

In [26]:
# Assemble dashboard visualization
display(Markdown("# Trading Dashboard"))
display(price_chart)
portfolio_evaluation_table + trade_evaluation_table

# Trading Dashboard

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

:Layout
   .Table.I  :Table   [index,Backtest]
   .Table.II :Table   [Stock,Entry Date,Exit Date,Shares,Entry Share Price,Exit Share Price,Entry Portfolio Holding,Exit Portfolio Holding,Profit/Loss]